In [1]:
import base as b
import pandas as pd
import hvplot.pandas  # noqa
import datetime as dt
from typing import Dict
import talib as ta
from constants import *
from scipy.stats import linregress
from logger_settings import logger
import holoviews as hv
import utils as ut

hv.extension('bokeh')
hv.notebook_extension('bokeh')

pd.options.plotting.backend = 'holoviews'

settings = {
    "ema_long_period": 45,
    "ema_xlong_period": 200,
    "ema_short_period": 10,
    "ema_xshort_period": 5,

    # Order Settings
    "quantity": 50,
}

instrument = b.Instrument(name="NIFTY 22650 CALL 7 Mar 2024")

SYMBOL = "NIFTY"
expiry = dt.datetime.strptime("2024-03-21", "%Y-%m-%d").date()
otype = "CE"
strike = 22000
date = dt.datetime.strptime("2024-03-15", "%Y-%m-%d").date()

tdf = ut.get_ticks(symbol=SYMBOL, expiry=expiry, strike=strike, otype=otype, date=date)

/home/nitin/nse-reports-trade/utils.py:28: DtypeWarning: Columns (14,15) have mixed types. Specify dtype option on import or set low_memory=False.
  scrip_df = pd.read_csv(file_path)


In [1]:
class EMAStrategy(b.Strategy):
    def __init__(self, instrument: "Instrument", settings: Dict):
        super().__init__(instrument, settings)
        self.om = b.OrderManager()

    def calculate_data(self):
        self.ticks["ema_long"] = ta.EMA(self.ticks.last_price, timeperiod=self.ema_long_period)
        self.ticks["ema_xlong"] = ta.EMA(self.ticks.last_price, timeperiod=self.ema_xlong_period)
        self.ticks["ema_short"] = ta.EMA(self.ticks.last_price, timeperiod=self.ema_short_period)
        self.ticks["ema_xshort"] = ta.EMA(self.ticks.last_price, timeperiod=self.ema_xshort_period)

    def entry_conditions(self) -> bool:
        last_tick = self.ticks.iloc[-1]
        # if not self.om.has_intrade_orders() and last_tick.ema_short > last_tick.ema_long and last_tick.ema_long > last_tick.ema_xlong:
        if not self.om.has_intrade_orders() and last_tick.ema_long > last_tick.ema_xlong and not self.exit_conditions():
            return True
        return False

    def exit_conditions(self) -> bool:
        if self.ticks.iloc[-1].ema_short <= self.ticks.iloc[-1].ema_long:
            return True
        return False

    def next(self, tick: Dict):
        super().next(tick)
        self.calculate_data()
        if self.entry_conditions():
            order = b.Order(type=b.Order.TYPE_BUY, limit_price=self.ticks.iloc[-1].last_price, created_at=self.ticks.iloc[-1].name, quantity=self.quantity, exchange_order_id=None)
            self.om.place_order(order)
        if self.exit_conditions():
            self.om.square_off_all_orders(index=self.ticks.iloc[-1].name, last_price=self.ticks.iloc[-1].last_price)


ps = EMAStrategy(instrument=instrument, settings=settings)
# for i in range(2000):
# for i in range(1293, 3221):
for i in range(tdf.shape[0]):
    ps.next(tdf.iloc[i].to_dict())


NameError: name 'b' is not defined

In [4]:
print(f"Total orders: {len(ps.om.closed_orders)}")
print(f"Total Avg PC %: {sum([order.pnl_pc for order in ps.om.closed_orders]) / len(ps.om.closed_orders)}")
print(f"Total profit %: {sum([order.pnl for order in ps.om.closed_orders]) * 100 / max([order.quantity * order.limit_price for order in ps.om.closed_orders])}")

Total orders: 276
Total Avg PC %: 0.044684207631318786
Total profit %: 8.36595920049454


In [3]:
# order_created_at = [ps.ticks.loc[order.created_at].id for order in ps.om.closed_orders]
# order_created_at_price = [ps.ticks.loc[order.created_at].last_price for order in ps.om.closed_orders]

# order_sqo_at = [ps.ticks.loc[order.square_off_at].id for order in ps.om.closed_orders]
# order_sqo_at_price = [ps.ticks.loc[order.square_off_at].last_price for order in ps.om.closed_orders]

def get_scaled_series(ser, mn):
    mx = mn + 50
    scaled_series = (((ser - ser.min()) / (ser.max() - ser.min())) * (mx - mn)) + mn
    return scaled_series

charts = [ps.ticks.hvplot.line(x='index', y=['last_price'], width=2000, height=1000, tools=['vline', 'crosshair'], hover_cols=['last_price', 'volume', 'index'])]
# charts.append(ps.ticks.hvplot.line(x='id', y='ema_xlong', color='brown', label='ema_xlong', line_width=3))
# charts.append(ps.ticks.hvplot.line(x='id', y='ema_long', color='orange', label='ema_long', line_width=2))
# charts.append(ps.ticks.hvplot.line(x='id', y='ema_short', color='purple', label='ema_short', line_width=1))
# charts.append(ps.ticks.hvplot.line(x='id', y='ema_xshort', color='brown', label='ema_xshort', line_width=.5))
ps.ticks["ch"] = ps.ticks.last_price.diff()
ps.ticks["vwch"] = ps.ticks.volume * ps.ticks.ch
# ps.ticks.loc[ps.ticks.ch <= 0, "vwch"] = -ps.ticks.volume
ps.ticks["adj_vol"] = get_scaled_series(ta.EMA(ps.ticks.vwch, timeperiod=10), ps.ticks.last_price.min() + 50)
# ps.ticks["adj_vol"] = get_scaled_series(ps.ticks.volume, ps.ticks.last_price.min() + 100)
charts.append(ps.ticks.hvplot.line(x='index', y='adj_vol', color='blue', label='vol', line_width=1, hover_cols=['volume', 'vwch']))


# orders = []
# for order in ps.om.closed_orders:
#     order_dict = order.__dict__
#     order_dict['created_id'] = ps.ticks.loc[order_dict['created_at']].id
#     order_dict['sq_id'] = ps.ticks.loc[order_dict['square_off_at']].id
#     orders.append(order_dict)

# odf = pd.DataFrame(orders)
# profit = odf.limit_price < odf.square_off_price
# charts.append(odf.loc[profit].hvplot.scatter(x='created_id', y='limit_price', color='green', marker='^', s=90, label='profit buy'))
# charts.append(odf.loc[profit].plot.scatter(x='sq_id', y='square_off_price', color='green', marker='v', s=90, label='profit sell'))
# charts.append(odf.loc[~profit].plot.scatter(x='created_id', y='limit_price', color='red', marker='^', s=90, label='loss buy'))
# charts.append(odf.loc[~profit].plot.scatter(x='sq_id', y='square_off_price', color='red', marker='v', s=90, label='loss sell'))

overlay = hv.Overlay(charts)
overlay

:Overlay
   .Curve.I   :Curve   [index]   (last_price,volume)
   .Curve.Vol :Curve   [index]   (adj_vol,volume,vwch)

In [6]:
import scipy as sc

# for idx in range(ps.ticks.shape[0]):
ps.ticks["minima"] = False

for idx in range(5000):
    peaks = sc.signal.argrelmin(ps.ticks.iloc[:idx+1].last_price.values, order=30)[0]
    peaks = peaks[peaks > idx - 2]
    ps.ticks.loc[peaks, "minima"] = True

ps.ticks["maxima"] = False
for idx in range(5000):
    peaks = sc.signal.argrelmax(ps.ticks.iloc[:idx+1].last_price.values, order=30)[0]
    peaks = peaks[peaks > idx - 2]
    ps.ticks.loc[peaks, "maxima"] = True

In [8]:
troughs_chart = ps.ticks.loc[ps.ticks.minima].hvplot.scatter(x='id', y='last_price', color='indigo', label='minima', marker='o', hover_cols='index')
peaks_chart = ps.ticks.loc[ps.ticks.maxima].hvplot.scatter(x='id', y='last_price', color='darkorange', label='maxima', marker='o', hover_cols='index')
vol_chart = ps.ticks.hvplot.line(x='id', y='adj_vol', color='blue', label='vol', line_width=1, hover_cols=['volume', 'vwch'])

overlay = hv.Overlay(charts + [peaks_chart, troughs_chart, vol_chart])
overlay
# peaks
# ps.ticks.loc[peaks[0]].hvplot.scatter(x='id', y='last_price', color='indigo', label='minima', marker='o', hover_cols='index')

:Overlay
   .Curve.I             :Curve   [id]   (last_price,volume,index)
   .Curve.Ema_xlong     :Curve   [id]   (ema_xlong)
   .Curve.Ema_long      :Curve   [id]   (ema_long)
   .Curve.Ema_short     :Curve   [id]   (ema_short)
   .Curve.Ema_xshort    :Curve   [id]   (ema_xshort)
   .Curve.Vol.I         :Curve   [id]   (adj_vol,volume,vwch)
   .Scatter.Profit_buy  :Scatter   [created_id]   (limit_price)
   .Scatter.Profit_sell :Scatter   [sq_id]   (square_off_price)
   .Scatter.Loss_buy    :Scatter   [created_id]   (limit_price)
   .Scatter.Loss_sell   :Scatter   [sq_id]   (square_off_price)
   .Scatter.Maxima      :Scatter   [id]   (last_price,index)
   .Scatter.Minima      :Scatter   [id]   (last_price,index)
   .Curve.Vol.II        :Curve   [id]   (adj_vol,volume,vwch)